#### 匯入套件

In [ ]:
import regex as re
import os
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.common.exceptions import TimeoutException, NoSuchElementException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from time import sleep

#### 設定選項

In [ ]:
my_options = webdriver.ChromeOptions()
my_options.add_argument('--disable-extensions')                     # 禁用瀏覽器擴展，減少干擾
my_options.add_argument('--disable-browser-side-navigation')        # 禁用瀏覽器側導航，提高穩定性
my_options.add_argument("--window-size=720,540")                  # 設定瀏覽器視窗大小
my_options.add_argument("--incognito")               # 開啟無痕模式
my_options.add_argument("--disable-popup-blocking")  # 禁用彈出攔截
my_options.add_argument("--disable-notifications")   # 取消 chrome 推播通知
my_options.add_argument("--lang=zh-TW")              # 設定為正體中文
# my_options.add_argument('--no-sandbox')                             # 禁用沙盒模式，提高在某些環境下的穩定性
# my_options.add_argument('--disable-dev-shm-usage')                  # 禁用/dev/shm使用，避免內存不足問題
# my_options.add_argument('--disable-gpu')                            # 禁用GPU加速，避免某些圖形相關問題
# my_options.add_argument('--disable-infobars')                       # 禁用信息欄，如"Chrome正在被自動化軟件控制"的提示
# my_options.add_argument('--disable-features=VizDisplayCompositor')  # 禁用視覺顯示合成器，解決某些渲染問題


# ===========設定 ChromeDriver 路徑 ===========
folderPath = 'project_gutenberg' # 儲存資料夾路徑 命名
if not os.path.exists(folderPath):  # 檢查資料夾是否存在，如果不存在則創建
    os.makedirs(folderPath)

#### 設定流程

In [ ]:
def visit(url):
    global driver
    driver = webdriver.Chrome(
    options=my_options
    )
    driver.get(url)
    sleep(3)

"""
url = input("請輸入要訪問的網址: ")
visit(url)
"""

def sanitize_filename(name):
    # 替換不合法字元為底線
    return re.sub(r'[\\/*?:"<>|()\[\]\r\n]+', "_", name).strip()

def parse():
    book = {}
    elements = driver.find_elements(
        By.CSS_SELECTOR, 'ul li.pgdbetext a[href]'
    )
    sleep(2)
    # 使用列表推導式提取每個元素的 href 屬性
    # return [element.get_attribute('href') for element in elements]
    # print(f"找到 {len(elements)} 個連結")
    for i in elements:
        try:
            # 取得標題並去除標題前後空白
            title = i.text.strip()
            if re.match(r'[\n\r\u4e00-\u9fff，。！？、：「」『』（）《》〈〉—…；．·～]+',title) == None:
                continue
            # print(title)
            s_title = sanitize_filename(title)
            # 取得 href 屬性並提取數字部分
            href_index = re.findall(r"\d+", i.get_attribute('href'))[0]
            href = f"https://www.gutenberg.org/cache/epub/{href_index}/pg{href_index}.txt"
            # 檢查標題和 href 是否有效
            # print(href)

            # 將標題和 href 添加到字典中
            book[s_title] = href
            
        except (AttributeError, IndexError):
            print("無法解析連結或標題")
            continue
    return book



def savetxt(title, content):
    if not os.path.exists(folderPath):
        os.makedirs(folderPath)
    with open(f"{folderPath}/{title}.txt", "w", encoding='utf-8') as file:
        if file.name in os.listdir(folderPath):
            print(f"{title}.txt 已存在，跳過保存")
        else:
            file.write(content)



def exit():
    global driver
    try:
        driver.quit()
    except Exception as e:
        print(f"退出瀏覽器時發生錯誤: {e}")
    finally:
        print("瀏覽器已關閉")

In [ ]:
# 變數儲存
dict_data = {}
chinese = r'[\u4e00-\u9fff，。！？、：「」『』（）《》〈〉—…；．·～]+'
count = 0

# ==== 下載書籍內容 ====
visit('https://www.gutenberg.org/browse/languages/zh')
books = parse()
for key, value in books.items():
    if count == 5:
        break
    print(f"正在下載 {key} ...")
    driver.get(value)
    sleep(1)  # 等待頁面加載
    # 使用正則表達式從頁面源碼中提取所有中文字符、標點符號等
    p = re.findall(chinese, driver.page_source)
    content = '\n'.join(p)
    # print(content)
    savetxt(key, content)
    print(f"{key} 下載完成")
    content = ""  # 清空 content 變數以釋放內存
    count += 1
exit()

正在下載 豆棚閒話 ...
['豆棚閒話', '弁言', '吾鄉先輩詩人徐菊潭有《豆棚吟》一冊，其所詠古風、律絕諸篇，俱宇宙古今奇情快', '事，久矣膾炙人口，惜乎人遐世遠、湮沒無傳，至今高人韻士每到秋風豆熟之際，誦', '其一二聯句，令人神往。', '餘不嗜作詩，乃檢遺事可堪解頤者，偶列數則，以補豆棚之意；仍以菊潭詩一首弁之', '，詩曰：閑著西邊一草堂，熱天無地可乘涼。', '池塘六月由來淺，林木三年未得長。栽得豆苗堪作蔭，勝於亭榭反生香。晚風約有溪', '南叟，劇對蟬聲話夕陽。', '第一則', '介之推火封妒婦', '江南地土窪下，雖屬卑溫，一交四月便值黃霉節氣，五月六月就是三伏炎天，酷日當', '空；無論行道之人汗流浹背，頭額焦枯，即在家住的也吼得氣喘，無處存著。上等除', '了富室大家，涼亭水閣，搖扇乘涼，安閑自在；次等便是山僧野叟，散發披襟，逍遙', '於長鬆蔭樹之下，方可過得；那些中等小家無計布擺，只得二月中旬覓得幾株羊眼豆', '，種在屋前屋後閑空地邊，或拿幾株木頭、幾根竹竿搭個棚子，搓些草索，周圍結彩', '的相似。', '不半月間，那豆藤在地上長將起來，彎彎曲曲依傍竹木隨著棚子牽纏滿了，卻比造的', '涼亭反透氣涼快。那些人家或老或少、或男或女，或拿根凳子，或掇張椅子，或鋪條', '涼蓆，隨高逐低坐在下面，搖著扇子，乘著風涼。鄉老們有說朝報的，有說新聞的，', '有說故事的。除了這些，男人便說人家內眷，某老娘賢，某大娘妒，大分說賢的少，', '說妒的多；那女人便說人家丈夫，某官人好，某漢子不好，大分愛丈夫的少，妒丈夫', '的多。可見『妒』之一字，男男女女日日在口裡提起、心裡轉動。如今我也不說別的', '，就把『妒』字說個暢炔，倒也不負這個搭豆棚的意思。你們且安心聽著。', '當日有幾個少年朋友同著幾個老成的人也坐在豆棚之下，右手拿著一把扇子，左手拿', '著不知甚麼閑書，看到鬧熱所在，有一首五言四句的詩，忽然把扇於在凳上一拍，叫', '將起來，便道：『說得太過！說得太過！』那老成人便立起身子道：『卻是為何？那', '少年便把書遞與他，一手指道：『他如何說「青竹蛇兒口，黃蜂尾上針。兩般猶未毒', '，最毒婦人心」？做待的人想是受了婦人閑氣，故意說得這樣利害。難道婦人的心比', '這二種惡物還毒些不成？』那老成人便接口說道：『你們後生小夥子不曾經